In [2]:
## Installation 
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import platform
import statsmodels.api as sm
from statsmodels.stats.outliers_influence import variance_inflation_factor
#워닝 메시지
import warnings
warnings.filterwarnings('ignore')


import platform
if platform.system() == "Darwin":          # MAC인 경우
    plt.rc('font', family ="AppleGothic")
else:
    plt.rc('font',family='Malgun Gothic')

#멧플로립에서 음수를 표시
plt.rc('axes',unicode_minus=False)

from sklearn.svm import SVC
from sklearn.model_selection import train_test_split,cross_val_score
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.model_selection import cross_val_score
from sklearn.ensemble import GradientBoostingRegressor, RandomForestRegressor
from sklearn.linear_model import LinearRegression
from sklearn.metrics import accuracy_score
from sklearn.model_selection import cross_val_score, KFold
from sklearn.preprocessing import MinMaxScaler 
import numpy as np

In [3]:
import os
current_directory = os.getcwd() # 현재 작업 디렉토리를 얻기
print("현재 작업 디렉토리:", current_directory)

현재 작업 디렉토리: c:\apps\miniproj


In [4]:
df= pd.read_csv('./Woo_data_3.csv', encoding='euc-kr')
df.columns

Index(['날짜', '위안화원_시', '유로달러_시', '코스피시가', '유로인덱스_시', '달러엔_시', '달러위안화_시',
       '달러원종가', '달러원시가', 'CD91', 'WTI', '달러인덱스', '콜금리', 'BIR', '엔원_시'],
      dtype='object')

In [8]:
X = df[['위안화원_시', '유로달러_시', 'WTI','달러위안화_시','달러엔_시','콜금리']] # 선택된 독립변수로 진행 
# X[['위안화원_시', '달러엔_시']] = np.log1p(X[['위안화원_시', '달러엔_시']]) # 왜도가 큰 두 변수를 로그 스켈링
y = df[['달러원종가']]
X_train, X_test, y_train, y_test = train_test_split( X, y, test_size=0.2, random_state=42)

pipeline = Pipeline([
    ('scaler',MinMaxScaler()),
    ('lr', LinearRegression())
	])
scores = cross_val_score(pipeline,X_train , y_train ,scoring='neg_mean_squared_error' ,  cv=5 )
scores.mean()

-44.21404895723945

In [83]:
from scipy import stats
for i in range(len(X.columns)):
    a = X[X.columns[i]]
    print(X.columns[i], len(a))
    statistic, p_value1 = stats.shapiro(a)
    alpha = 0.05  # 유의수준 설정 (일반적으로 0.05 사용)
    if p_value1 < alpha:
        print('shapiro p_value:', p_value1, "데이터는 정규 분포를 따르지 않습니다.")
    else:
        print('shapiro p_value:', p_value1, "데이터는 정규 분포를 따를 가능성이 있습니다.")
    
    statistic, p_value2 = stats.normaltest(a)
    if p_value2 < alpha:
        print('normaltest p_value:', p_value2, "데이터는 정규 분포를 따르지 않습니다.")
    else:
        print('normaltest p_value:', p_value2, "데이터는 정규 분포를 따를 가능성이 있습니다.")

위안화원_시 3318
shapiro p_value: 5.489284140409166e-32 데이터는 정규 분포를 따르지 않습니다.
normaltest p_value: 5.532271546404854e-49 데이터는 정규 분포를 따르지 않습니다.
유로달러_시 3318
shapiro p_value: 2.1404088069283473e-33 데이터는 정규 분포를 따르지 않습니다.
normaltest p_value: 1.4510778192077149e-134 데이터는 정규 분포를 따르지 않습니다.
WTI 3318
shapiro p_value: 2.0446130815016056e-23 데이터는 정규 분포를 따르지 않습니다.
normaltest p_value: 4.5395559656160794e-39 데이터는 정규 분포를 따르지 않습니다.
달러위안화_시 3318
shapiro p_value: 5.543413788579503e-28 데이터는 정규 분포를 따르지 않습니다.
normaltest p_value: 9.678326636784534e-157 데이터는 정규 분포를 따르지 않습니다.
달러엔_시 3318
shapiro p_value: 2.1619078962470123e-30 데이터는 정규 분포를 따르지 않습니다.
normaltest p_value: 0.02074495647644517 데이터는 정규 분포를 따르지 않습니다.
콜금리 3318
shapiro p_value: 8.236924015081933e-32 데이터는 정규 분포를 따르지 않습니다.
normaltest p_value: 1.2067091143991562e-140 데이터는 정규 분포를 따르지 않습니다.


In [6]:
#  교차검증 + LinearRegression

# 데이터 불러오기 및 특성과 대상 변수 정의
X = df[['위안화원_시', '유로달러_시', 'WTI','달러위안화_시','달러엔_시','콜금리']]
y = df[['달러원종가']]

# 다양한 테스트 세트 크기를 시도하기 위한 비율 리스트
test_sizes = [0.1, 0.2, 0.3, 0.4, 0.5,0.6,0.7,0.8]

# 교차 검증 설정
n_splits = 5  # 폴드(Fold)의 수 
random_state = 42  # 시드(seed) 값 (재현성을 위해 사용)

# 모델 및 스케일러 초기화 
regressor = LinearRegression()
scaler = MinMaxScaler()
pipeline = Pipeline([
    ('scaler', scaler),
    ('regressor', regressor)
])

# 다양한 테스트 세트 크기에 대한 결과 저장
results = {}

for test_size in test_sizes:
    # 테스트 세트 크기 설정
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=test_size, random_state=random_state)

    # 교차 검증 수행 및 성능 평가 
    scores = cross_val_score(pipeline, X_train, y_train, cv=KFold(n_splits=n_splits, shuffle=True, random_state=random_state), scoring='neg_mean_squared_error')
    
    # 평균 제곱 오차의 평균값 저장
    mean_mse = -scores.mean()
    
    # 결과 저장
    results[test_size] = mean_mse

# 결과 출력
for test_size, mse in results.items():
    print(f"Test Size: {test_size}, Mean Squared Error: {mse:.4f}")


Test Size: 0.1, Mean Squared Error: 208.5228
Test Size: 0.2, Mean Squared Error: 44.0872
Test Size: 0.3, Mean Squared Error: 43.8370
Test Size: 0.4, Mean Squared Error: 43.7995
Test Size: 0.5, Mean Squared Error: 43.4576
Test Size: 0.6, Mean Squared Error: 42.8811
Test Size: 0.7, Mean Squared Error: 42.7734
Test Size: 0.8, Mean Squared Error: 46.0825


In [7]:
grid.best_params_

AttributeError: 'GridSearchCV' object has no attribute 'best_params_'

In [85]:
#  교차검증 + GradientBoostingRegressor


# 데이터 불러오기 및 특성과 대상 변수 정의 (사용자에게 맞게 변경하세요)
X_1 = df[['위안화원_시', '유로달러_시', 'WTI','달러위안화_시','달러엔_시','콜금리']]
y_1 = df[['달러원종가']]

# 다양한 테스트 세트 크기를 시도하기 위한 비율 리스트 (사용자에게 맞게 변경 가능)
test_sizes = [0.1, 0.2, 0.3, 0.4, 0.5,0.6,0.7,0.8]

# 교차 검증 설정
n_splits_1 = 5  # 폴드(Fold)의 수 (사용자에게 맞게 변경 가능)
random_state_1 = 42  # 시드(seed) 값 (재현성을 위해 사용)

# 모델 및 스케일러 초기화 (사용자가 원하는 모델 및 스케일러로 변경 가능)
GB = GradientBoostingRegressor()
scaler = MinMaxScaler()
pipeline = Pipeline([
    ('scaler', scaler),
    ('GB', GB)
])

# 다양한 테스트 세트 크기에 대한 결과 저장
results = {}

for test_size in test_sizes:
    # 테스트 세트 크기 설정
    X_train_1, X_test_1, y_train_1, y_test_1  = train_test_split(X_1, y_1, test_size=test_size, random_state=random_state)

    # 교차 검증 수행 및 성능 평가 (이 예제에서는 평균 제곱 오차를 사용)
    scores_1 = cross_val_score(pipeline, X_train_1, y_train_1, 
                            cv=KFold(n_splits=n_splits_1, 
                            shuffle=True, random_state=random_state_1), 
                             scoring='neg_mean_squared_error')
    
    # 평균 제곱 오차의 평균값 저장
    mean_mse = -scores_1.mean()
    
    # 결과 저장
    results[test_size] = mean_mse

# 결과 출력
for test_size, mse in results.items():
    print(f"Test Size: {test_size}, Mean Squared Error: {mse:.4f}")

KeyboardInterrupt: 

In [ ]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import LinearRegression
from lightgbm import LGBMRegressor
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.feature_selection import RFE

In [ ]:
#  교차검증 + RandomForestRegressor
X_2 = df[['위안화원_시', '유로달러_시', 'WTI','달러위안화_시','달러엔_시','콜금리']]
y_2 = df[['달러원종가']]

# 다양한 테스트 세트 크기를 시도하기 위한 비율 리스트 (사용자에게 맞게 변경 가능)
test_sizes = [0.1, 0.2, 0.3, 0.4, 0.5,0.6,0.7,0.8]

# 교차 검증 설정
n_splits_2 = 5  # 폴드(Fold)의 수 (사용자에게 맞게 변경 가능)
random_state_2 = 42  # 시드(seed) 값 (재현성을 위해 사용)

# 모델 및 스케일러 초기화 (사용자가 원하는 모델 및 스케일러로 변경 가능)
sclaer = MinMaxScaler()
rf=RandomForestRegressor()


pipe = Pipeline([
    ('scaler',sclaer),
    ('model', rf)
])

param = {
    'model__max_depth': [4, 5, 6, 7],
    'model__min_samples_leaf' : [1, 2, 3, 4, 5, 6]
}

grid = GridSearchCV(estimator=pipe, param_grid=param, cv=3)
grid.fit(X_train,y_train)


# 다양한 테스트 세트 크기에 대한 결과 저장
results = {}

for test_size in test_sizes:
    # 테스트 세트 크기 설정
    X_train_2, X_test_2, y_train_2, y_test_2  = train_test_split(X_2, y_2, test_size=test_size, random_state=random_state)

    # 교차 검증 수행 및 성능 평가 
    scores_2 = cross_val_score(pipeline, X_train_2, y_train_2, 
                            cv=KFold(n_splits=n_splits_2, 
                            shuffle=True, random_state=random_state_2), 
                             scoring='neg_mean_squared_error')
    
    # 평균 제곱 오차의 평균값 저장
    mean_mse = -scores_1.mean()
    
    # 결과 저장
    results[test_size] = mean_mse

# 결과 출력
for test_size, mse in results.items():
    print(f"Test Size: {test_size}, Mean Squared Error: {mse:.4f}")

Test Size: 0.1, Mean Squared Error: 85.5644
Test Size: 0.2, Mean Squared Error: 85.5644
Test Size: 0.3, Mean Squared Error: 85.5644
Test Size: 0.4, Mean Squared Error: 85.5644
Test Size: 0.5, Mean Squared Error: 85.5644
Test Size: 0.6, Mean Squared Error: 85.5644
Test Size: 0.7, Mean Squared Error: 85.5644
Test Size: 0.8, Mean Squared Error: 85.5644


In [ ]:
grid.best_params_

{'model__max_depth': 7, 'model__min_samples_leaf': 1}

레이블(대상 변수)이 연속적인 실수값인 회귀 문제를 해결하기 위해 다양한 회귀 모델을 사용할 수 있습니다. 어떤 모델을 선택할지는 데이터와 문제의 특성에 따라 다를 수 있지만, 아래에 일반적으로 사용되는 회귀 모델 중 일부를 나열하겠습니다:

1. **선형 회귀 (Linear Regression)**:
   - 데이터 간의 선형 관계를 모델링하는 가장 간단한 회귀 모델입니다.
   - 예측값은 입력 특성의 선형 조합으로 계산됩니다.
   - Ridge Regression, Lasso Regression 등과 같은 정규화된 선형 회귀 모델도 있습니다.

2. **결정 트리 회귀 (Decision Tree Regression)**:
   - 데이터를 분할하여 트리 구조로 모델링하는 방법입니다.
   - 데이터의 비선형 관계를 잘 모델링할 수 있습니다.

3. **랜덤 포레스트 회귀 (Random Forest Regression)**:
   - 여러 개의 결정 트리를 앙상블한 모델로, 예측의 안정성과 정확도를 높일 수 있습니다.

4. **그래디언트 부스팅 회귀 (Gradient Boosting Regression)**:
   - 여러 개의 약한 예측 모델을 조합하여 강력한 예측 모델을 만드는 앙상블 기법입니다.
   - 예를 들어, XGBoost, LightGBM, CatBoost와 같은 라이브러리를 사용할 수 있습니다.

5. **서포트 벡터 머신 회귀 (Support Vector Machine Regression)**:
   - 주어진 데이터 포인트와 가장 가까운 서포트 벡터들 사이의 마진을 최대화하는 회귀 모델입니다.

6. **신경망 기반 회귀 (Neural Network Regression)**:
   - 딥 러닝 기술을 활용하여 복잡한 비선형 관계를 모델링할 수 있습니다.
   - 인공 신경망을 사용하는 방법 중 하나입니다.

모델 선택은 데이터의 특성, 모델의 복잡성, 예측 정확도, 계산 비용 등을 고려하여 결정해야 합니다. 또한 하이퍼파라미터 튜닝과 교차 검증을 사용하여 모델의 성능을 최적화할 수 있습니다. 문제에 가장 적합한 모델을 선택하려면 데이터와 문제의 도메인에 대한 이해가 중요합니다.

In [13]:
from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import LinearRegression
from lightgbm import LGBMRegressor
from sklearn.pipeline import Pipeline
from sklearn.model_selection import GridSearchCV
from sklearn.feature_selection import RFE

sclaer = MinMaxScaler()
lgb=LGBMRegressor()
feature = RFE(LinearRegression(), n_features_to_select=7)

pipe = Pipeline([
    ('scaler',sclaer),
    ('feature_select',feature),
    ('model', lgb)
])

param = {
    'model__learning_rate' : [0.2, 0.14, 0.15, 0.16, 0.1],
    'model__max_depth': [6, 7, 8, 9],
    'model__min_split_gain' : [4, 5, 6],
    'model__n_estimator' : [10, 20, 30]    
}

grid = GridSearchCV(estimator=pipe, param_grid=param, cv=5)
grid.fit(X_train,y_train)
print(grid.best_params_)

[LightGBM] [Warning] Unknown parameter: n_estimator
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Warning] Unknown parameter: n_estimator
[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000228 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1430
[LightGBM] [Info] Number of data points in the train set: 2123, number of used features: 6
[LightGBM] [Info] Start training from score 1150.348746
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain

In [ ]:
grid.best_params_

{'model__learning_rate': 0.15, 'model__max_depth': 6}

In [ ]:
y_pred=grid.predict(X_test)

[LightGBM] [Warning] Accuracy may be bad since you didn't explicitly set num_leaves OR 2^max_depth > num_leaves. (num_leaves=31).


In [ ]:
best_learning_rate = grid.best_params_['model__learning_rate']
best_max_depth = grid.best_params_['model__max_depth']

best_lgb_model = LGBMRegressor(learning_rate=best_learning_rate, max_depth=best_max_depth)

In [ ]:
best_learning_rate

0.15

In [ ]:
best_max_depth

6